In [1]:
import streamlit_functions as sf
import importlib as imp
import geopandas as gpd
import matplotlib.pyplot as plt
import functions as f
# debugging
import importlib as imp
imp.reload(f)

from shapely.geometry import MultiLineString



In [2]:
bikelane_all = gpd.read_parquet('dataset/raw_unprocessed/bikelane_dk_crs_25832.parquet')

# filtering bikelanes which goes through a forest area

In [6]:
# ok we cant read in a 150 MB multilinestring for sure. Fuck
# bikelane_all_mp_wgs84 = gpd.read_parquet('dataset/raw_unprocessed/bikelane_wgs84_multilinestring.parquet')
bikelane_all_wgs84 = gpd.read_parquet('dataset/raw_unprocessed/bikelane_dk_WGS84_h3_indexed.parquet') 
forest_all_wgs84 = gpd.read_parquet('dataset/raw_unprocessed/denmark_landuse_forest_crs_wgs84.parquet')

In [16]:
# Assuming bikelane_all_wgs84 and forest_all_wgs84 are already loaded as GeoDataFrames

# Step 1: Perform the spatial join
intersected_forests = gpd.sjoin(forest_all_wgs84, bikelane_all_wgs84, how="inner", op='intersects')

# Remove any duplicates based on geometries directly to ensure uniqueness
# Convert geometries to WKT string which is hashable and can be used to drop duplicates
intersected_forests['geometry_wkt'] = intersected_forests.geometry.apply(lambda x: x.wkt)
forest_areas_with_bikelanes = intersected_forests.drop_duplicates(subset='geometry_wkt')

# Remove the helper column and retain the original GeoDataFrame format
forest_areas_with_bikelanes = forest_areas_with_bikelanes.drop(columns=['geometry_wkt'])

C:\Users\Gergo Gyori\AppData\Roaming\Python\Python312\site-packages\IPython\core\interactiveshell.py:3493: FutureWarning: The `op` parameter is deprecated and will be removed in a future release. Please use the `predicate` parameter instead.
  if await self.run_code(code, result, async_=asy):


In [20]:
forest_areas_with_bikelanes.drop(columns=['index_right0', 'index_right1', 'index_right2', 'h3_index'], inplace=True)

In [29]:
forest_areas_with_bikelanes.to_parquet('dataset/processed/forest_areas_with_bikelanes_wgs84_TEMP.parquet')

### Quick check

In [25]:
forest_areas_with_bikelanes.sample(5000).explore()